In [1]:
import os
import numpy as np
import pandas as pd
import tensorflow as tf
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.layers import Input, Conv2D, BatchNormalization, Activation, Add, MaxPooling2D, GlobalAveragePooling2D, Dense, Reshape, Permute, Multiply
from tensorflow.keras.models import Model
from tensorflow.keras.optimizers import Adam
from sklearn.ensemble import VotingClassifier

# Define paths
train_dir = r'E:\sem2\deep learning\train\train'
test_dir = r'E:\sem2\deep learning\test\test'
output_folder = r'E:\sem2\deep learning\New folder\New folder' 

# Create output folder if it doesn't exist
os.makedirs(output_folder, exist_ok=True)

# Get subfolder names as category names
category_names = sorted(os.listdir(train_dir))

# Define constants
input_shape = (64, 64, 3)  # Input shape
batch_size = 32
num_classes = len(category_names)

# Data preprocessing and augmentation
train_datagen = ImageDataGenerator(
    rescale=1./255,
    shear_range=0.2,
    zoom_range=0.2,
    horizontal_flip=True
)

train_generator = train_datagen.flow_from_directory(
    train_dir,
    target_size=(input_shape[0], input_shape[1]),
    batch_size=batch_size,
    class_mode='categorical',
    shuffle=True
)

# Define ResNet-like model
def residual_block(x, filters, strides=(1, 1), downsample=False):
    identity = x
    stride_conv = strides[0] if isinstance(strides, tuple) else strides

    x = Conv2D(filters=filters, kernel_size=(5, 5), strides=strides, padding='same')(x)
    x = BatchNormalization()(x)
    x = Activation('relu')(x)

    x = Conv2D(filters=filters, kernel_size=(5, 5), padding='same')(x)
    x = BatchNormalization()(x)

    if downsample:
        identity = Conv2D(filters=filters, kernel_size=(1, 1), strides=stride_conv, padding='same')(identity)
        identity = BatchNormalization()(identity)

    x = Add()([x, identity])
    x = Activation('relu')(x)
    return x

inputs = Input(shape=input_shape)
x = Conv2D(filters=64, kernel_size=(5, 5), strides=(2, 2), padding='same')(inputs)
x = BatchNormalization()(x)
x = Activation('relu')(x)
x = MaxPooling2D(pool_size=(3, 3), strides=(2, 2), padding='same')(x)

x = residual_block(x, filters=64)
x = residual_block(x, filters=64)
x = residual_block(x, filters=64)

x = residual_block(x, filters=128, strides=(2, 2), downsample=True)
x = residual_block(x, filters=128)
x = residual_block(x, filters=128)

x = residual_block(x, filters=256, strides=(2, 2), downsample=True)
x = residual_block(x, filters=256)
x = residual_block(x, filters=256)

# Add self-attention mechanism
x_global_avg = GlobalAveragePooling2D()(x)
x_reshape = Reshape((1, 1, 256))(x_global_avg)
x_attention = Conv2D(filters=256, kernel_size=(1, 1), activation='relu')(x)
x_attention = Conv2D(filters=256, kernel_size=(1, 1), activation='sigmoid')(x_attention)
x_attention = Multiply()([x, x_attention])
x_attention = Add()([x, x_attention])

x = GlobalAveragePooling2D()(x_attention)
outputs = Dense(num_classes, activation='softmax')(x)

model = Model(inputs, outputs)

# Compile model
optimizer = Adam(learning_rate=0.0001)
model.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])

# Train the model on GPU
model.fit(
    train_generator,
    epochs=180,
    steps_per_epoch=train_generator.samples // batch_size,
    verbose=1
)

# Prediction on test data using ensemble
test_images = sorted(os.listdir(test_dir))  # Sort test images
num_runs = 5  # Number of ensemble runs

for i, image_name in enumerate(test_images):
    img_path = os.path.join(test_dir, image_name)
    predictions = []

    for _ in range(num_runs):
        # Load and preprocess the image
        img = tf.keras.preprocessing.image.load_img(img_path, target_size=(input_shape[0], input_shape[1]))
        img_array = tf.keras.preprocessing.image.img_to_array(img)
        img_array = np.expand_dims(img_array, axis=0) / 255.0
        
        # Predict
        prediction = model.predict(img_array)
        predictions.append(np.argmax(prediction))

    # Get the mode of predictions
    mode_prediction = np.bincount(predictions).argmax()
    category_name = category_names[mode_prediction]

    # Save prediction as a separate CSV file
    df = pd.DataFrame([(image_name, category_name)], columns=['ID', 'Category'])
    df.to_csv(os.path.join(output_folder, f'fa1prediction_{i + 1}.csv'), index=False)


Found 65000 images belonging to 50 classes.
Epoch 1/180


C:\Users\adhit\AppData\Roaming\Python\Python311\site-packages\keras\src\trainers\data_adapters\py_dataset_adapter.py:120: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


2031/2031 ━━━━━━━━━━━━━━━━━━━━ 2976s 1s/step - accuracy: 0.1940 - loss: 3.1875
Epoch 2/180
2031/2031 ━━━━━━━━━━━━━━━━━━━━ 1s 21us/step - accuracy: 0.2812 - loss: 1.3482    
Epoch 3/180


c:\ProgramData\anaconda3\Lib\contextlib.py:155: UserWarning: Your input ran out of data; interrupting training. Make sure that your dataset or generator can generate at least `steps_per_epoch * epochs` batches. You may need to use the `.repeat()` function when building your dataset.
  self.gen.throw(typ, value, traceback)


2031/2031 ━━━━━━━━━━━━━━━━━━━━ 1151s 566ms/step - accuracy: 0.3704 - loss: 2.3033
Epoch 4/180
2031/2031 ━━━━━━━━━━━━━━━━━━━━ 1s 5us/step - accuracy: 0.3438 - loss: 1.0659     
Epoch 5/180
2031/2031 ━━━━━━━━━━━━━━━━━━━━ 1064s 523ms/step - accuracy: 0.4418 - loss: 2.0332
Epoch 6/180
2031/2031 ━━━━━━━━━━━━━━━━━━━━ 0s 5us/step - accuracy: 0.4688 - loss: 0.9105     
Epoch 7/180
2031/2031 ━━━━━━━━━━━━━━━━━━━━ 1069s 526ms/step - accuracy: 0.4862 - loss: 1.8500
Epoch 8/180
2031/2031 ━━━━━━━━━━━━━━━━━━━━ 1s 6us/step - accuracy: 0.4375 - loss: 1.1149     
Epoch 9/180
2031/2031 ━━━━━━━━━━━━━━━━━━━━ 1127s 554ms/step - accuracy: 0.5226 - loss: 1.7058
Epoch 10/180
2031/2031 ━━━━━━━━━━━━━━━━━━━━ 1s 5us/step - accuracy: 0.4062 - loss: 0.9789     
Epoch 11/180
2031/2031 ━━━━━━━━━━━━━━━━━━━━ 1292s 635ms/step - accuracy: 0.5542 - loss: 1.5694
Epoch 12/180
2031/2031 ━━━━━━━━━━━━━━━━━━━━ 1s 5us/step - accuracy: 0.5938 - loss: 0.6199     
Epoch 13/180
2031/2031 ━━━━━━━━━━━━━━━━━━━━ 1070s 526ms/step - accura